In [97]:
import pandas as pd
import numpy as np
import pyspark
import os
import folium

from pyspark.sql import *
from pyspark.sql.functions import to_timestamp, when
from pyspark.sql.types import *

In [116]:
spark = SparkSession.builder.getOrCreate()
sc = spark.sparkContext

from pyspark.sql import SQLContext
sqlContext = SQLContext(sc)

folder = 'C:\\Users\\Matyas\\Documents\\FEL\\Lausanne\\ada\\proj\\ADA_Project\\data\\'
folder_out = 'C:\\Users\\Matyas\\Documents\\FEL\\Lausanne\\ada\\proj\\ADA_Project\\output\\'

In [103]:
txt_file = sc.textFile(folder + 'UrlToCountry\\GdeltDomainsByCountry-May18.txt')

In [104]:
rdd = txt_file.map(lambda x: x.split("\t"))
url_sources = rdd.toDF(['web', 'code', 'country'])
url_sources_pd = url_sources.toPandas()

In [105]:
# so far for the first 100 top countries
wrong_codes = ['GM','GA','GB','UK','RS','AU','AS','CN','CH','SV','ES','SP','TU','KN','SC','SE','SW','ZA','SF','UP','JA','SZ','IS','EZ','EI','VM','PO','CI','KR','KS','RP','DA','NU','NE','NG','NI','nic','SN','SG','sig','LO','IC','TK','TL','BM','BD','BG','BU','EN','LI','LS','LT','LH','BY','BO','RI','LG','MC','MN','MG','MA','MO','moc','CE','MU','PA','PM','LE','AJ','ZI','CJ','IZ','BH','BA','BK','BL','AG','YM','DO','DR','TO','TN','TS','GG','HA','WA','CB','BF','SU','KU','GJ','MP','GV','IV','ST','TP','TT','TD','NS','AV','AC','HO','CD','BC','TI','UV','CG','CF','RQ','AN','BN','MJ','KV','MI','FP','VI','VT','BX','MH','GQ','EK','PP','OD','WZ','VQ','GK','NH','SX','CK','TX','KT','PS','CT','AQ','AA','BP','CW','PC','MB','AY','CQ','PU','MF','RM','NT','FS','WE','FG']
right_codes = ['DE','GM','GA','GB','RU','AT','AU','KM','CN','SJ','SV','ES','TR','KP','KN','SC','SE','ZM','ZA','UA','JP','CH','IL','CZ','IE','VN','PT','CL','KI','KR','PH','DK','nic','NU','NE','NG','NI','sig','SN','SG','SK','IS','TC','TK','MM','BM','BD','BG','EE','LR','LI','LS','LT','BI','BY','RS','LV','moc','MC','MN','MG','MA','MO','LK','OM','PY','PA','LB','AZ','ZW','KY','IQ','BZ','BH','BA','BO','DZ','YE','DM','DO','TG','TO','TN','GE','HT','NA','KH','BS','SD','KW','GD','MU','GN','CI','LC','ST','TP','TT','SR','AI','AG','HN','TD','BW','TJ','BF','CD','CG','PR','AD','BJ','ME','XK','MW','PF','VG','VA','BN','MS','GU','GQ','PG','SS','SZ','VI','GG','VU','GS','CC','TM','CX','PW','CF','AS','AW','SB','CK','PN','MQ','AQ','MP','GW','YT','MH','AN','FQ','PS','GF']

#print('code\twrong\tright')
#for code in wrong_codes:
#    if code in right_codes:
#        if wrong_codes.index(code) >= right_codes.index(code):
#            print(code + '\t' + str(wrong_codes.index(code)) + '\t' + str(right_codes.index(code)))

corr_codes = pd.DataFrame({'wrong': wrong_codes, 'right': right_codes}, columns=['wrong', 'right'])

invalid_codes = ['CV','RB','OS','TT']
for code in invalid_codes:
    url_sources_pd = url_sources_pd[url_sources_pd['code'] != code]
    
url_sources_corr = pd.merge(url_sources_pd, corr_codes, how='left', left_on='code', right_on='wrong')
url_sources_corr.loc[url_sources_corr['right'].isnull(), 'right'] = url_sources_corr['code']
url_sources_corr.head()

web code        country wrong right
0     0-100.it   IT          Italy   NaN    IT
1      0-50.ru   RS         Russia    RS    RU
2  0-60mag.com   US  United States   NaN    US
3   0-debt.com   US  United States   NaN    US
4   000fff.org   US  United States   NaN    US

In [106]:
url_sources_corr = url_sources_corr.drop(['code', 'wrong'], axis=1)
url_sources_corr = url_sources_corr.rename(index=str, columns={'right': 'code'})
url_sources_corr.head()

web        country code
0     0-100.it          Italy   IT
1      0-50.ru         Russia   RU
2  0-60mag.com  United States   US
3   0-debt.com  United States   US
4   000fff.org  United States   US

In [107]:
url_sum = url_sources_corr.groupby(['country', 'code'], as_index=False).count()
url_sum = url_sum.sort_values('web', ascending=False)
url_sum.head()

country code    web
225   United States   US  56160
224  United Kingdom   GB  14892
177          Russia   RU   8216
103           Italy   IT   7672
38           Canada   CA   7331

In [109]:
country_info = pd.read_csv(folder + 'CountryCodes\\countries-info.csv')
country_info = country_info[['name', 'alpha-2', 'alpha-3', 'region', 'sub-region']]
country_info.head(5)

name alpha-2 alpha-3   region       sub-region
0     Afghanistan      AF     AFG     Asia    Southern Asia
1   Åland Islands      AX     ALA   Europe  Northern Europe
2         Albania      AL     ALB   Europe  Southern Europe
3         Algeria      DZ     DZA   Africa  Northern Africa
4  American Samoa      AS     ASM  Oceania        Polynesia

In [110]:
df_urls = pd.merge(country_info, url_sources_corr, left_on='alpha-2', right_on='code')
df_urls = df_urls.drop(['country', 'code'], axis=1)
#df_urls.to_csv('./urls.csv')
df_urls.head()

name alpha-2 alpha-3 region     sub-region                web
0  Afghanistan      AF     AFG   Asia  Southern Asia   108worldnews.com
1  Afghanistan      AF     AFG   Asia  Southern Asia             1tv.af
2  Afghanistan      AF     AFG   Asia  Southern Asia         1tvnews.af
3  Afghanistan      AF     AFG   Asia  Southern Asia         aff.org.af
4  Afghanistan      AF     AFG   Asia  Southern Asia  afghan-review.com

In [111]:
df_urls_sum = df_urls.groupby(['name', 'alpha-2', 'alpha-3', 'region', 'sub-region'], as_index=False).count()
df_urls_sum = df_urls_sum.sort_values('web', ascending=False)
df_urls_sum['web-log'] = np.log(df_urls_sum['web'])
df_urls_sum.head()

name alpha-2 alpha-3  \
217                           United States of America      US     USA   
216  United Kingdom of Great Britain and Northern I...      GB     GBR   
171                                 Russian Federation      RU     RUS   
103                                              Italy      IT     ITA   
36                                              Canada      CA     CAN   

       region        sub-region    web    web-log  
217  Americas  Northern America  56160  10.935960  
216    Europe   Northern Europe  14892   9.608579  
171    Europe    Eastern Europe   8216   9.013839  
103    Europe   Southern Europe   7672   8.945333  
36   Americas  Northern America   7331   8.899867

In [57]:
events = sqlContext.read.parquet(folder + 'Results\\CountryEvent_number.parquet').toPandas()
reports = sqlContext.read.parquet(folder + 'Results\\CountrySource_number.parquet').toPandas()
codeconv_fips = pd.read_csv(folder + 'CountryCodes\\CountryCode_FIPS_alpha.csv')
codeconv_info = pd.read_csv(folder + 'CountryCodes\\countries-info.csv')
codeconv_info = codeconv_info[['name', 'alpha-2', 'alpha-3', 'region', 'sub-region']]

In [89]:
events_a2 = pd.merge(events, codeconv_fips, left_on='ActionGeo_CountryCode', right_on='FIPS_GDELT')
events_a3 = pd.merge(events_a2, codeconv_info, left_on='alpha-2', right_on='alpha-2')
events_a3 = events_a3[['name', 'alpha-2', 'alpha-3', 'count']]
events_a3['count-log'] = np.log(events_a3['count'])
events_a3['count-norm'] = (events_a3['count-log'] - events_a3['count-log'].min())/(events_a3['count-log'].max() - events_a3['count-log'].min())


reports_a3 = pd.merge(reports, codeconv_info, left_on='country_source', right_on='name')
reports_a3 = reports_a3[['name', 'alpha-2', 'alpha-3', 'count']]
reports_a3['count-log'] = np.log(reports_a3['count'])
reports_a3['count-norm'] = (reports_a3['count-log'] - reports_a3['count-log'].min())/(reports_a3['count-log'].max() - reports_a3['count-log'].min())

reports_a3.head()

name alpha-2 alpha-3  \
0                               United Arab Emirates      AE     ARE   
1  United Kingdom of Great Britain and Northern I...      GB     GBR   
2                                        South Sudan      SS     SSD   
3        Macedonia (the former Yugoslav Republic of)      MK     MKD   
4                                 Russian Federation      RU     RUS   

      count  count-log  count-norm  
0   2612158  14.775687    0.747163  
1  32445043  17.295058    0.874561  
2     98207  11.494833    0.581260  
3    119705  11.692786    0.591270  
4   3269313  15.000090    0.758511

In [118]:
import branca.colormap as cm

def plot_map(df, col, save=False, fileName=None):

    world_map = folder + 'Visualizations\\countries-land-10km.geo.json'

    color_scale = cm.linear.YlOrRd_04.to_step(40).scale(min(df[col]), max(df[col]))

    def get_color(code):
        country = df[df['alpha-3'] == code]['name'].count()
        if country == 0:
            # print(code)
            return '#8c8c8c' # MISSING -> gray
        else:
            return color_scale(int(df[df['alpha-3'] == code][col]))

    m = folium.Map(location=[46.8, 8.3], tiles='cartodbpositron', zoom_start=2)
    folium.GeoJson(
        data = world_map,
        style_function = lambda feature: {
            'fillColor': get_color(feature['properties']['A3']),
            'fillOpacity': 0.7,
            'color' : 'black',
            'weight' : 1,
        }    
    ).add_to(m)
    m.add_child(color_scale)
    
    if save and fileName is not None:
        m.save(outfile = folder_out + fileName + '.html')
    
    return m

In [119]:
plot_map(df_urls_sum, 'web-log', True, 'urls-log')

In [120]:
plot_map(reports_a3, 'count-log', True, 'reports-log')

In [121]:
plot_map(events_a3, 'count-log', True, 'events-log')